RAG Chatbot Evaluation Testing.

In [ ]:
!pip install langchain
!pip install langchain-core
!pip install langchain-community
!pip install langchain-text-splitters==0.0.1
!pip install dataset
!pip install ragas
!pip install replicate
!pip install colab-xterm
!pip install nest_asyncio
!pip install supabase
!pip install sentence-transformers==2.2.2
!pip install docx2txt
!pip install pypdf==4.2.0
!pip install PyPDF2==3.0.1
!pip install faiss-cpu==1.7.4

In [2]:
from supabase import create_client

supabase = create_client()

In [4]:
!mkdir data

In [7]:
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain_community.embeddings import HuggingFaceEmbeddings
from langchain_community.vectorstores import FAISS
import os

def get_data():
    dir_path = "./data/"
    contents = os.listdir(dir_path)
    files_in_local = [f for f in contents if os.path.isfile(os.path.join(dir_path, f))]
    files = supabase.storage.from_("test-data").list()
    file_in_storage = [file['name'] for file in files]

    file_to_delete = list(set(files_in_local) - set(file_in_storage))
    file_to_download = list(set(file_in_storage) - set(files_in_local))

    for file in file_to_delete:
        try:
            os.remove(dir_path+file)
            print("removed", file)
        except:
            print("error removing file")
    for file in file_to_download:
        with open('./data/'+file, 'wb+') as f:
            res = supabase.storage.from_('test-data').download(file)
            f.write(res)

def load_docs():
    from langchain_community.document_loaders import PyPDFLoader, TextLoader, Docx2txtLoader
    documents = []
    for file in os.listdir("data"):
        if file.endswith(".pdf"):
            pdf_path = "./data/" + file
            loader = PyPDFLoader(pdf_path)
            documents.extend(loader.load())
        elif file.endswith('.docx') or file.endswith('.doc'):
            doc_path = "./data/" + file
            loader = Docx2txtLoader(doc_path)
            documents.extend(loader.load())
        elif file.endswith('.txt'):
            text_path = "./data/" + file
            loader = TextLoader(text_path)
            documents.extend(loader.load())
    return documents

def process_documents(docs):
    text_splitter = RecursiveCharacterTextSplitter(chunk_size=1000, chunk_overlap=200)
    text_chunks = text_splitter.split_documents(docs)

    return text_chunks

#download data from supabase
get_data()

#load documents
docs = load_docs()

#process documents
chunks = process_documents(docs)

In [23]:
dataset = [
    {
        'question': 'Apa visi dari Program Studi Manajemen Informatika?',
        'ground_truths': 'Visi Program Studi Manajemen Informatika adalah menjadi program studi pendidikan vokasional terbaik tingkat nasional di bidang Sistem Informasi, bermartabat, dan berwawasan internasional pada tahun 2025.',
        'answer': 'Visi Program Studi Manajemen Informatika adalah sebagai berikut:\n\n"Pada tahun 2025 menjadi program studi pendidikan vokasional terbaik tingkat nasional di bidang Sistem Informasi, bermartabat, dan berwawasan internasional."',
        'contexts': ['Visi Program Studi Manajemen Informatika adalah sebagai berikut:\n\n"Pada tahun 2025 menjadi program studi pendidikan vokasional terbaik tingkat nasional di bidang Sistem Informasi, bermartabat, dan berwawasan internasional."']
    },
    {
        'question': 'Apa mata kuliah yang dipelajari pada semester 1 di Program Studi Teknik Komputer?',
        'ground_truths': 'Mata Kuliah Semester 1 Program Studi Teknik Komputer meliputi Matematika Diskret, Jaringan Komputer Dasar, It Essential, Algoritma Pemrograman, Basis Data, Komunikasi Data, dan Elektronika Dasar.',
        'answer': 'Mata Kuliah Semester 1 Program Studi Teknik Komputer:\n\n1. Matematika Diskret (CEN2101) dengan 2 SKS dan 2 jam teori\n2. Jaringan Komputer Dasar (CEN3101) dengan 2 SKS dan 4 jam teori/praktik\n3. It Essential (CEN3102) dengan 3 SKS dan 7 jam teori/praktik\n4. Algoritma Pemrograman (CEN3103) dengan 5 SKS dan 9 jam teori/praktik\n5. Basis Data (CEN3104) dengan 3 SKS dan 5 jam teori/praktik\n6. Komunikasi Data (CEN3105) dengan 2 SKS dan 2 jam teori\n7. Elektronika Dasar (CEN3106) dengan 2 SKS dan 4 jam teori/praktik',
        'contexts': ['Mata Kuliah Semester 1 Program Studi Teknik Komputer: Matematika Diskret (CEN2101) dengan 2 SKS dan 2 jam teori, Jaringan Komputer Dasar (CEN3101) dengan 2 SKS dan 4 jam teori/praktik, It Essential (CEN3102) dengan 3 SKS dan 7 jam teori/praktik, Algoritma Pemrograman (CEN3103) dengan 5 SKS dan 9 jam teori/praktik, Basis Data (CEN3104) dengan 3 SKS dan 5 jam teori/praktik, Komunikasi Data (CEN3105) dengan 2 SKS dan 2 jam teori, serta Elektronika Dasar (CEN3106) dengan 2 SKS dan 4 jam teori/praktik.']
    },
    {
        'question': 'Apa profil lulusan Program Studi D3 Manajemen Informatika?',
        'ground_truths':'Profil lulusan Program Studi D3 Manajemen Informatika adalah Programmer, Web Developer, dan Mobile Application Developer.',
        'answer': 'Profil lulusan Program Studi D3 Manajemen Informatika berdasarkan jenjang KKNI, rekomendasi APTIKOM, peta okupasi TIK Kominfo, serta survei kebutuhan industri adalah Programmer, Web Developer, dan Mobile Application Developer.',
        'contexts': ['Profil lulusan Program Studi D3 Manajemen Informatika berdasarkan jenjang KKNI, rekomendasi APTIKOM, peta okupasi TIK Kominfo, serta survei kebutuhan industri adalah Programmer, Web Developer, dan Mobile Application Developer.']
    },
    {
        'question': 'Apa hasil survei tracer study terhadap alumni Program Studi Manajemen Informatika?',
        'ground_truths':'Hasil survei tracer study menunjukkan bahwa 47% dari 85 responden membutuhkan waktu kurang dari 6 bulan untuk mendapatkan pekerjaan dan 62% responden mendapatkan pekerjaan yang sesuai dengan program studi.',
        'answer': 'Program Studi Manajemen Informatika telah melaksanakan tracer study terhadap alumni dan pengguna alumni untuk evaluasi kurikulum. Hasil survei 3 tahun terakhir menunjukkan bahwa 47% dari 85 responden membutuhkan waktu kurang dari 6 bulan untuk mendapatkan pekerjaan. Pada pertanyaan tentang kesesuaian bidang kerja dengan profil bidang studi sistem informasi, 62% responden Program Studi Manajemen Informatika mendapatkan pekerjaan yang sesuai dengan program studi.',
        'contexts': ['Program Studi Manajemen Informatika telah melaksanakan tracer study terhadap alumni dan pengguna alumni untuk evaluasi kurikulum. Tracer study berupa survei ini bertujuan untuk mengetahui kesesuaian kurikulum dengan pekerjaan yang diperoleh di lapangan atau di perusahaan. Fokus utama adalah kesesuaian dengan visi misi Program Studi Manajemen Informatika, capaian pembelajaran kurikulum sistem informasi, kemampuan penguasaan, penerapan teori, serta etos kerja yang dipelajari selama studi.\n\nHasil survei 3 tahun terakhir menunjukkan bahwa 47% dari 85 responden membutuhkan waktu kurang dari 6 bulan untuk mendapatkan pekerjaan.\n\nPada pertanyaan tentang kesesuaian bidang kerja dengan profil bidang studi sistem informasi, 62% responden Program Studi Manajemen Informatika mendapatkan pekerjaan yang sesuai dengan program studi.']
    },
    {
        'question': 'Bagaimana kemampuan lulusan Program Studi Manajemen Informatika dalam bersaing di pasar kerja internasional?',
        'ground_truths':'80% alumni Program Studi Manajemen Informatika mendapatkan pekerjaan di perusahaan bertaraf multinasional, menunjukkan kemampuan bersaing secara internasional.',
        'answer': 'Berdasarkan survei, dapat disimpulkan bahwa lulusan Program Studi Manajemen Informatika dapat bekerja di perusahaan kompetitif dengan posisi yang variatif. 80% alumni Program Studi Manajemen Informatika mendapatkan pekerjaan di perusahaan bertaraf multinasional, menunjukkan bahwa kurikulum mampu membekali lulusan untuk bersaing secara internasional.',
        'contexts': ['Berdasarkan survei, dapat disimpulkan bahwa lulusan Program Studi Manajemen Informatika dapat bekerja di perusahaan kompetitif dengan posisi yang variatif. 80% alumni Program Studi Manajemen Informatika mendapatkan pekerjaan di perusahaan bertaraf multinasional, menunjukkan bahwa kurikulum mampu membekali lulusan untuk bersaing secara internasional.']
    },
    {
        'question': 'Apa mata kuliah yang dipelajari pada semester 2 di Program Studi Teknik Komputer?',
        'ground_truths':'Mata Kuliah Semester 2 Program Studi Teknik Komputer meliputi Matematika dan Statistika, Switching, Routing dan Wireless, Sistem Operasi, Web Dasar, Pemrograman Mobile, Pemrograman Berbasis Objek (PBO), Sistem Digital, dan Organisasi dan Arsitektur Komputer.',
        'answer': 'Mata Kuliah Semester 2 Program Studi Teknik Komputer:\n\n1. Matematika dan Statistika (CEN2201) dengan 3 SKS dan 3 jam teori\n2. Switching, Routing dan Wireless (CEN3201) dengan 3 SKS dan 5 jam teori/praktik\n3. Sistem Operasi (CEN3202) dengan 3 SKS dan 5 jam teori/praktik\n4. Web Dasar (CEN3203) dengan 3 SKS dan 7 jam teori/praktik\n5. Pemrograman Mobile (CEN3204) dengan 2 SKS dan 4 jam teori/praktik\n6. Pemrograman Berbasis Objek (PBO) (CEN3205) dengan 3 SKS dan 5 jam teori/praktik\n7. Sistem Digital (CEN3206) dengan 2 SKS dan 4 jam teori/praktik\n8. Organisasi dan Arsitektur Komputer (CEN3207) dengan 2 SKS dan 2 jam teori',
        'contexts': ['Mata Kuliah Semester 2 Program Studi Teknik Komputer: Matematika dan Statistika (CEN2201) dengan 3 SKS dan 3 jam teori, Switching, Routing dan Wireless (CEN3201) dengan 3 SKS dan 5 jam teori/praktik, Sistem Operasi (CEN3202) dengan 3 SKS dan 5 jam teori/praktik, Web Dasar (CEN3203) dengan 3 SKS dan 7 jam teori/praktik, Pemrograman Mobile (CEN3204) dengan 2 SKS dan 4 jam teori/praktik, Pemrograman Berbasis Objek (PBO) (CEN3205) dengan 3 SKS dan 5 jam teori/praktik, Sistem Digital (CEN3206) dengan 2 SKS dan 4 jam teori/praktik, serta Organisasi dan Arsitektur Komputer (CEN3207) dengan 2 SKS dan 2 jam teori.']
    },
    {
        'question': 'Apa visi dari Program Studi Teknik Komputer?',
        'ground_truths':'Visi Program Studi Teknik Komputer adalah menjadi institusi pendidikan vokasional terbaik tingkat nasional di bidang Teknik Komputer Jaringan pada tahun 2025.',
        'answer': 'Visi Program Studi Teknik Komputer adalah sebagai berikut:\n\n"Pada tahun 2025, Program studi Teknik Komputer bertujuan menjadi institusi pendidikan vokasional terbaik tingkat nasional di bidang Teknik Komputer Jaringan, yang bermartabat dan berwawasan internasional."',
        'contexts': ['Visi Program Studi Teknik Komputer adalah sebagai berikut:\n\n"Pada tahun 2025, Program studi Teknik Komputer bertujuan menjadi institusi pendidikan vokasional terbaik tingkat nasional di bidang Teknik Komputer Jaringan, yang bermartabat dan berwawasan internasional."']
    },
    {
        'question': 'Apa mata kuliah yang dipelajari pada semester 1 di Program Studi Teknologi Rekayasa Perangkat Lunak (TRPL)?',
        'ground_truths':'Mata Kuliah Semester 1 Program Studi Teknologi Rekayasa Perangkat Lunak (TRPL) meliputi Pengantar Teknologi Komputer dan Informasi, Basis Data, Aljabar Linear, Algoritma dan Pemrograman, Agama, serta Sistem Informasi.',
        'answer': 'Mata Kuliah Semester 1 Program Studi Teknologi Rekayasa Perangkat Lunak (TRPL):\n\n1. Pengantar Teknologi Komputer dan Informasi (RPL1101) dengan 4 SKS dan 8 jam teori/praktik\n2. Basis Data (RPL2101) dengan 4 SKS dan 8 jam teori/praktik\n3. Aljabar Linear (RPL2102) dengan 3 SKS dan 3 jam teori\n4. Algoritma dan Pemrograman (RPL3101) dengan 5 SKS dan 9 jam teori/praktik\n5. Agama (RPL3102) dengan 2 SKS dan 2 jam teori\n6. Sistem Informasi (RPL3103) dengan 2 SKS dan 2 jam teori',
        'contexts': ['Mata Kuliah Program Studi Teknologi Rekayasa Perangkat Lunak (TRPL) Semester 1 adalah sebagai berikut : Pada semester pertama, mahasiswa akan mempelajari mata kuliah Pengantar Teknologi Komputer dan Informasi (RPL1101) dengan 4 SKS dan 8 jam teori/praktik, Basis Data (RPL2101) dengan 4 SKS dan 8 jam teori/praktik, Aljabar Linear (RPL2102) dengan 3 SKS dan 3 jam teori, Algoritma dan Pemrograman (RPL3101) dengan 5 SKS dan 9 jam teori/praktik, Agama (RPL3102) dengan 2 SKS dan 2 jam teori, serta Sistem Informasi (RPL3103) dengan 2 SKS dan 2 jam teori.']
    },
    {
        'question': 'Apa mata kuliah yang dipelajari pada semester 2 di Program Studi Teknologi Rekayasa Perangkat Lunak (TRPL)?',
        'ground_truths':'Mata Kuliah Semester 2 Program Studi Teknologi Rekayasa Perangkat Lunak (TRPL) meliputi Sistem Operasi, Matematika Diskrit, Struktur Data, Komunikasi Data dan Jaringan, Sistem Basis Data, Pemrograman Berorientasi Objek, dan Pengantar Rekayasa Perangkat Lunak.',
        'answer': 'Mata Kuliah Semester 2 Program Studi Teknologi Rekayasa Perangkat Lunak (TRPL):\n\n1. Sistem Operasi (RPL2201) dengan 3 SKS dan 5 jam teori/praktik\n2. Matematika Diskrit (RPL2202) dengan 3 SKS dan 3 jam teori\n3. Struktur Data (RPL3201) dengan 2 SKS dan 4 jam teori/praktik\n4. Komunikasi Data dan Jaringan (RPL3202) dengan 3 SKS dan 5 jam teori/praktik\n5. Sistem Basis Data (RPL3203) dengan 3 SKS dan 5 jam teori/praktik\n6. Pemrograman Berorientasi Objek (RPL3204) dengan 4 SKS dan 8 jam teori/praktik\n7. Pengantar Rekayasa Perangkat Lunak (RPL3205) dengan 2 SKS dan 2 jam teori',
        'contexts': ['Mata Kuliah Program Studi Teknologi Rekayasa Perangkat Lunak (TRPL) Semester 2 adalah sebagai berikut: Pada semester kedua, mahasiswa akan melanjutkan dengan mata kuliah Sistem Operasi (RPL2201) dengan 3 SKS dan 5 jam teori/praktik, Matematika Diskrit (RPL2202) dengan 3 SKS dan 3 jam teori, Struktur Data (RPL3201) dengan 2 SKS dan 4 jam teori/praktik, Komunikasi Data dan Jaringan (RPL3202) dengan 3 SKS dan 5 jam teori/praktik, Sistem Basis Data (RPL3203) dengan 3 SKS dan 5 jam teori/praktik, Pemrograman Berorientasi Objek (RPL3204) dengan 4 SKS dan 8 jam teori/praktik, serta Pengantar Rekayasa Perangkat Lunak (RPL3205) dengan 2 SKS dan 2 jam teori.']
    },
    {
        'question': 'Apa tujuan dari tracer study yang dilakukan oleh Program Studi Manajemen Informatika?',
        'ground_truths':'Tujuan dari tracer study adalah untuk mengetahui kesesuaian kurikulum dengan pekerjaan yang diperoleh di lapangan atau di perusahaan, serta evaluasi capaian pembelajaran kurikulum sistem informasi, kemampuan penguasaan, penerapan teori, serta etos kerja yang dipelajari selama studi.',
        'answer': 'Program Studi Manajemen Informatika telah melaksanakan tracer study terhadap alumni dan pengguna alumni untuk evaluasi kurikulum. Tracer study berupa survei ini bertujuan untuk mengetahui kesesuaian kurikulum dengan pekerjaan yang diperoleh di lapangan atau di perusahaan. Fokus utama adalah kesesuaian dengan visi misi Program Studi Manajemen Informatika, capaian pembelajaran kurikulum sistem informasi, kemampuan penguasaan, penerapan teori, serta etos kerja yang dipelajari selama studi.',
        'contexts': ['Program Studi Manajemen Informatika telah melaksanakan tracer study terhadap alumni dan pengguna alumni untuk evaluasi kurikulum. Tracer study berupa survei ini bertujuan untuk mengetahui kesesuaian kurikulum dengan pekerjaan yang diperoleh di lapangan atau di perusahaan. Fokus utama adalah kesesuaian dengan visi misi Program Studi Manajemen Informatika, capaian pembelajaran kurikulum sistem informasi, kemampuan penguasaan, penerapan teori, serta etos kerja yang dipelajari selama studi.']
    }
]


In [24]:
import pandas as pd

test_data = pd.DataFrame(dataset)

In [25]:
test_data

question  \
0  Apa visi dari Program Studi Manajemen Informat...   
1  Apa mata kuliah yang dipelajari pada semester ...   
2  Apa profil lulusan Program Studi D3 Manajemen ...   
3  Apa hasil survei tracer study terhadap alumni ...   
4  Bagaimana kemampuan lulusan Program Studi Mana...   
5  Apa mata kuliah yang dipelajari pada semester ...   
6       Apa visi dari Program Studi Teknik Komputer?   
7  Apa mata kuliah yang dipelajari pada semester ...   
8  Apa mata kuliah yang dipelajari pada semester ...   
9  Apa tujuan dari tracer study yang dilakukan ol...   

                                       ground_truths  \
0  Visi Program Studi Manajemen Informatika adala...   
1  Mata Kuliah Semester 1 Program Studi Teknik Ko...   
2  Profil lulusan Program Studi D3 Manajemen Info...   
3  Hasil survei tracer study menunjukkan bahwa 47...   
4  80% alumni Program Studi Manajemen Informatika...   
5  Mata Kuliah Semester 2 Program Studi Teknik Ko...   
6  Visi Program Studi Teknik Komputer adalah menj...   
7  Mata Kuliah Semester 1 Program Studi Teknologi...   
8  Mata Kuliah Semester 2 Program Studi Teknologi...   
9  Tujuan dari tracer study adalah untuk mengetah...   

                                              answer  \
0  Visi Program Studi Manajemen Informatika adala...   
1  Mata Kuliah Semester 1 Program Studi Teknik Ko...   
2  Profil lulusan Program Studi D3 Manajemen Info...   
3  Program Studi Manajemen Informatika telah mela...   
4  Berdasarkan survei, dapat disimpulkan bahwa lu...   
5  Mata Kuliah Semester 2 Program Studi Teknik Ko...   
6  Visi Program Studi Teknik Komputer adalah seba...   
7  Mata Kuliah Semester 1 Program Studi Teknologi...   
8  Mata Kuliah Semester 2 Program Studi Teknologi...   
9  Program Studi Manajemen Informatika telah mela...   

                                            contexts  
0  [Visi Program Studi Manajemen Informatika adal...  
1  [Mata Kuliah Semester 1 Program Studi Teknik K...  
2  [Profil lulusan Program Studi D3 Manajemen Inf...  
3  [Program Studi Manajemen Informatika telah mel...  
4  [Berdasarkan survei, dapat disimpulkan bahwa l...  
5  [Mata Kuliah Semester 2 Program Studi Teknik K...  
6  [Visi Program Studi Teknik Komputer adalah seb...  
7  [Mata Kuliah Program Studi Teknologi Rekayasa ...  
8  [Mata Kuliah Program Studi Teknologi Rekayasa ...  
9  [Program Studi Manajemen Informatika telah mel...

Running Llama from Ollama

In [11]:
%load_ext colabxterm

In [12]:
%xterm

Launching Xterm...

<IPython.core.display.Javascript object>

In [13]:
from langchain_community.llms import Ollama
from langchain.embeddings.huggingface import HuggingFaceEmbeddings

generator_llm = Ollama(model="llama3")
critic_llm    = Ollama(model="llama3")
embeddings    = HuggingFaceEmbeddings(model_name="LazarusNLP/congen-indo-e5-small",  model_kwargs={'device': 'cpu'})

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:139: LangChainDeprecationWarning: The class `HuggingFaceEmbeddings` was deprecated in LangChain 0.2.2 and will be removed in 0.3.0. An updated version of the class exists in the langchain-huggingface package and should be used instead. To use it run `pip install -U langchain-huggingface` and import as `from langchain_huggingface import HuggingFaceEmbeddings`.
  warn_deprecated(
/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


.gitattributes:   0%|          | 0.00/1.56k [00:00<?, ?B/s]

config.json:   0%|          | 0.00/681 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/471M [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/53.0 [00:00<?, ?B/s]

...

pytorch_model.bin:   0%|          | 0.00/1.18M [00:00<?, ?B/s]

README.md:   0%|          | 0.00/2.54k [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/123 [00:00<?, ?B/s]

eval/similarity_evaluation_results.csv:   0%|          | 0.00/3.30k [00:00<?, ?B/s]

modules.json:   0%|          | 0.00/354 [00:00<?, ?B/s]

In [26]:
#for now its unused
for document in chunks:
    document.metadata['file_name'] = document.metadata['source']

In [27]:
from langchain_community.vectorstores import FAISS

vectorstore = FAISS.from_documents(chunks, embeddings)
retriever = vectorstore.as_retriever()

In [28]:
from langchain_core.prompts import PromptTemplate

template = """<|begin_of_text|>
            <|start_header_id|>
                system
            <|end_header_id|>
                You are an assistant of technology information department of politeknik negeri padang to answer
                questions related to the user's document.If the user tries to ask out of
                topic questions do not engange in the conversation.If the given context
                is not sufficient to answer the question,Do not answer the question. Generate the next agent response by answering the question in indonesian's language.
            <|eot_id|>
            <|start_header_id|>
                user
            <|end_header_id|>
                Answer the user question based on the context provided below
                Context :{context}
                Question: {question}
            <|eot_id|>
            <|start_header_id|>
                assistant
            <|end_header_id|>
        """

prompt = PromptTemplate(
    template=template,
    input_variables=["context","question"]
  )

In [29]:
from langchain.schema.runnable import RunnablePassthrough
from langchain.schema.output_parser import StrOutputParser

rag_chain = (
    {"context": retriever,  "question": RunnablePassthrough()}
    | prompt
    | generator_llm
    | StrOutputParser()
)

In [30]:
questions = test_data["question"].to_list()
ground_truth = test_data["ground_truths"].to_list()

In [31]:
from datasets import Dataset

questions = test_data["question"].to_list()
ground_truth = test_data["ground_truths"].to_list()

data = {"question": [], "answer": [], "contexts": [], "ground_truth": ground_truth}

for query in questions:
    data["question"].append(query)
    data["answer"].append(rag_chain.invoke(query))
    data["contexts"].append([doc.page_content for doc in retriever.get_relevant_documents(query)])

dataset = Dataset.from_dict(data)

In [32]:
dataset.to_pandas()

question  \
0  Apa visi dari Program Studi Manajemen Informat...   
1  Apa mata kuliah yang dipelajari pada semester ...   
2  Apa profil lulusan Program Studi D3 Manajemen ...   
3  Apa hasil survei tracer study terhadap alumni ...   
4  Bagaimana kemampuan lulusan Program Studi Mana...   
5  Apa mata kuliah yang dipelajari pada semester ...   
6       Apa visi dari Program Studi Teknik Komputer?   
7  Apa mata kuliah yang dipelajari pada semester ...   
8  Apa mata kuliah yang dipelajari pada semester ...   
9  Apa tujuan dari tracer study yang dilakukan ol...   

                                              answer  \
0  Berdasarkan dokumen Visi_Program_Studi_Manajem...   
1  Berdasarkan konteks dokumen, mata kuliah yang ...   
2  Berdasarkan informasi yang tersedia, Profil lu...   
3  Berdasarkan dokumen yang tersedia, hasil surve...   
4  Berdasarkan data Tracer Study, dapat disimpulk...   
5  Berdasarkan konteks yang tersedia, mata kuliah...   
6  Berdasarkan dokumen "Visi dan Misi Program Stu...   
7  Berdasarkan informasi yang tersedia, pada Seme...   
8  Berdasarkan konteks, pada Semester 2 di Progra...   
9  Tujuan dari Tracer Study yang dilakukan oleh P...   

                                            contexts  \
0  [Visi Program Studi Manajemen Informatika adal...   
1  [Mata Kuliah Program Studi Teknik Komputer\n\n...   
2  [Profil lulusan Program Studi D3 Manajemen Inf...   
3  [Program Studi Manajemen Informatika telah mel...   
4  [Berdasarkan survei, dapat disimpulkan bahwa l...   
5  [Mata Kuliah Semester 2 Program Studi Teknik K...   
6  [Visi Program Studi Teknik Komputer adalah seb...   
7  [Mata Kuliah Program Studi Teknologi Rekayasa ...   
8  [Mata Kuliah Program Studi Teknologi Rekayasa ...   
9  [Program Studi Manajemen Informatika telah mel...   

                                        ground_truth  
0  Visi Program Studi Manajemen Informatika adala...  
1  Mata Kuliah Semester 1 Program Studi Teknik Ko...  
2  Profil lulusan Program Studi D3 Manajemen Info...  
3  Hasil survei tracer study menunjukkan bahwa 47...  
4  80% alumni Program Studi Manajemen Informatika...  
5  Mata Kuliah Semester 2 Program Studi Teknik Ko...  
6  Visi Program Studi Teknik Komputer adalah menj...  
7  Mata Kuliah Semester 1 Program Studi Teknologi...  
8  Mata Kuliah Semester 2 Program Studi Teknologi...  
9  Tujuan dari tracer study adalah untuk mengetah...

In [36]:
data2 = [2,3]
data3 = [4,5]
data4 = [6,7]
data5 = [8]

In [46]:
from concurrent.futures import thread
from ragas import evaluate
from ragas.metrics import (
    faithfulness,
    answer_relevancy,
    context_recall,
    context_precision,
)
from ragas import RunConfig
import nest_asyncio

thread_timeout = 120

nest_asyncio.apply()

result = evaluate(
    dataset = dataset.select(range(2)),
    metrics=[
        context_precision,
        context_recall,
        faithfulness,
        answer_relevancy,
    ],
    llm=generator_llm,embeddings=embeddings,
    run_config=RunConfig(thread_timeout=thread_timeout)
)

Evaluating:   0%|          | 0/8 [00:00<?, ?it/s]

In [47]:
result2 = evaluate(
    dataset = dataset.select(data2),
    metrics=[
        context_precision,
        context_recall,
        faithfulness,
        answer_relevancy,
    ],
    llm=generator_llm,embeddings=embeddings,
    run_config=RunConfig(thread_timeout=thread_timeout)
)

Evaluating:   0%|          | 0/8 [00:00<?, ?it/s]

In [48]:
result3 = evaluate(
    dataset = dataset.select(data3),
    metrics=[
        context_precision,
        context_recall,
        faithfulness,
        answer_relevancy,
    ],
    llm=generator_llm,embeddings=embeddings,
    run_config=RunConfig(thread_timeout=thread_timeout)
)

Evaluating:   0%|          | 0/8 [00:00<?, ?it/s]

In [49]:
result4 = evaluate(
    dataset = dataset.select(data4),
    metrics=[
        context_precision,
        context_recall,
        faithfulness,
        answer_relevancy,
    ],
    llm=generator_llm,embeddings=embeddings,
    run_config=RunConfig(thread_timeout=thread_timeout)
)

Evaluating:   0%|          | 0/8 [00:00<?, ?it/s]

In [50]:
result5 = evaluate(
    dataset = dataset.select(data5),
    metrics=[
        context_precision,
        context_recall,
        faithfulness,
        answer_relevancy,
    ],
    llm=generator_llm,embeddings=embeddings,
    run_config=RunConfig(thread_timeout=thread_timeout)
)

Evaluating:   0%|          | 0/4 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/ragas/evaluation.py:304: RuntimeWarning: Mean of empty slice
  value = np.nanmean(self.scores[cn])


In [56]:
result.to_pandas().drop(columns=['contexts'])

question  \
0  Apa visi dari Program Studi Manajemen Informat...   
1  Apa mata kuliah yang dipelajari pada semester ...   

                                              answer  \
0  Berdasarkan dokumen Visi_Program_Studi_Manajem...   
1  Berdasarkan konteks dokumen, mata kuliah yang ...   

                                        ground_truth  context_precision  \
0  Visi Program Studi Manajemen Informatika adala...           0.916667   
1  Mata Kuliah Semester 1 Program Studi Teknik Ko...           0.750000   

   context_recall  faithfulness  answer_relevancy  
0             1.0           0.5          0.892332  
1             1.0           0.0          0.922909

In [57]:
result2.to_pandas().drop(columns=['contexts'])

question  \
0  Apa profil lulusan Program Studi D3 Manajemen ...   
1  Apa hasil survei tracer study terhadap alumni ...   

                                              answer  \
0  Berdasarkan informasi yang tersedia, Profil lu...   
1  Berdasarkan dokumen yang tersedia, hasil surve...   

                                        ground_truth  context_precision  \
0  Profil lulusan Program Studi D3 Manajemen Info...           0.916667   
1  Hasil survei tracer study menunjukkan bahwa 47...           0.916667   

   context_recall  faithfulness  answer_relevancy  
0             1.0           1.0          0.811703  
1             1.0           0.6          0.611010

In [58]:
result3.to_pandas().drop(columns=['contexts'])

question  \
0  Bagaimana kemampuan lulusan Program Studi Mana...   
1  Apa mata kuliah yang dipelajari pada semester ...   

                                              answer  \
0  Berdasarkan data Tracer Study, dapat disimpulk...   
1  Berdasarkan konteks yang tersedia, mata kuliah...   

                                        ground_truth  context_precision  \
0  80% alumni Program Studi Manajemen Informatika...                1.0   
1  Mata Kuliah Semester 2 Program Studi Teknik Ko...                1.0   

   context_recall  faithfulness  answer_relevancy  
0             0.5          0.75          0.772468  
1             NaN          1.00          0.947524

In [59]:
result4.to_pandas().drop(columns=['contexts'])

question  \
0       Apa visi dari Program Studi Teknik Komputer?   
1  Apa mata kuliah yang dipelajari pada semester ...   

                                              answer  \
0  Berdasarkan dokumen "Visi dan Misi Program Stu...   
1  Berdasarkan informasi yang tersedia, pada Seme...   

                                        ground_truth  context_precision  \
0  Visi Program Studi Teknik Komputer adalah menj...           0.833333   
1  Mata Kuliah Semester 1 Program Studi Teknologi...           1.000000   

   context_recall  faithfulness  answer_relevancy  
0             1.0         0.500          0.885868  
1             NaN         0.875          0.856642

In [60]:
result5.to_pandas().drop(columns=['contexts'])

question  \
0  Apa mata kuliah yang dipelajari pada semester ...   

                                              answer  \
0  Berdasarkan konteks, pada Semester 2 di Progra...   

                                        ground_truth  context_precision  \
0  Mata Kuliah Semester 2 Program Studi Teknologi...           0.833333   

   context_recall  faithfulness  answer_relevancy  
0             NaN           0.5          0.867524